Demo ipynb for LDA

Testing the pipeline for a single game

In [1]:
import pandas as pd
import numpy as np

from pathlib import Path

import gensim

import spacy

import nltk

import pyLDAvis
import pickle
from datetime import datetime

In [2]:
# download nltk stopwords
# import nltk
# nltk.download('stopwords')

In [3]:
# load a dataset

dataset_path = Path('../../dataset/topic_modelling/top_10_games/00_Terraria.pkl')

# dataset_path = Path('../dataset_cleaned_heartless_sampled_for_demo.pkl')

# dataset_path = Path('../../dataset/topic_modelling/top_11_genres/01_Indie.pkl')


dataset = pd.read_pickle(dataset_path)

dataset.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
Index: 75499 entries, 57735 to 133233
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   index         75499 non-null  int64 
 1   app_id        75499 non-null  int64 
 2   app_name      75499 non-null  object
 3   review_text   75499 non-null  object
 4   review_score  75499 non-null  int64 
 5   review_votes  75499 non-null  int64 
dtypes: int64(4), object(2)
memory usage: 4.0+ MB


In [4]:
%load_ext autoreload

In [5]:
# data preprocessing

import re

import sys
sys.path.append('../../sa')

%autoreload 2
import str_cleaning_functions

def cleaning(df, review):
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_links2(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.clean(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.deEmojify(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_non_letters(x))
    df[review] = df[review].apply(lambda x: x.lower())
    df[review] = df[review].apply(lambda x: str_cleaning_functions.unify_whitespaces(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.remove_stopword(x))
    df[review] = df[review].apply(lambda x: str_cleaning_functions.unify_whitespaces(x))

def cleaning_strlist(str_list):
    str_list = list(map(lambda x: str_cleaning_functions.remove_links(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.remove_links2(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.clean(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.deEmojify(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.remove_non_letters(x), str_list))
    str_list = list(map(lambda x: x.lower(), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.unify_whitespaces(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.remove_stopword(x), str_list))
    str_list = list(map(lambda x: str_cleaning_functions.unify_whitespaces(x), str_list))
    return str_list

In [6]:
# apply data preprocessing

cleaning(dataset, 'review_text')

In [7]:
X = dataset['review_text'].values

In [8]:
X

array(['werewolf riding unicorn shooting rainbows gun build teleporters find hair dresser spider cavern get sword shoots cats take lord moon using yoyo summon sharknado minion shoots sharks enemies find sky temples air wyverns spawn buy music box wizard go record music like playing base whenever want go build castle made entirely white marble would seem thing minecraft game dimension trust get used start learning game terraria simply one satisfying sandbox experiences may sound rude compared minecraft imagination',
       'copies game go around giving people look sad', 'introduction',
       ...,
       'game game start newb get pro hours entertainment even get bored get mods newb',
       'far one greatest games played yet',
       'game awesome eye cthulhu possible'], dtype=object)

In [9]:
# nltk.download('averaged_perceptron_tagger')
# t = nltk.word_tokenize(X[0])
# tt = nltk.pos_tag(t)
# tt

In [10]:
# do lemmatization, but not stemming (as part of speech is important in topic modelling)
# use nltk wordnet for lemmatization

from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet

lemma = WordNetLemmatizer()

# from https://stackoverflow.com/questions/25534214/nltk-wordnet-lemmatizer-shouldnt-it-lemmatize-all-inflections-of-a-word

# from: https://www.cnblogs.com/jclian91/p/9898511.html
def get_wordnet_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return None     # if none -> created as noun by wordnet
    
def lemmatization(text):
   # use nltk to get PoS tag
    tagged = nltk.pos_tag(nltk.word_tokenize(text))

    # then we only need adj, adv, verb, noun
    # convert from nltk Penn Treebank tag to wordnet tag
    wn_tagged = list(map(lambda x: (x[0], get_wordnet_pos(x[1])), tagged))

    # lemmatize by the PoS
    lemmatized = list(map(lambda x: lemma.lemmatize(x[0], pos=x[1] if x[1] else wordnet.NOUN), wn_tagged))
    # lemma.lemmatize(wn_tagged[0], pos=wordnet.NOUN)

    return lemmatized

In [11]:
# lemmatize the data

X_lemmatized = list(map(lambda x: lemmatization(x), X))


# filter empty list of strings in X_lemmatized, as they are not useful for topic modelling
X_lemmatized = list(filter(lambda x: len(x) > 0, X_lemmatized))

In [11]:
X_lemmatized[0]

['game',
 'bill',
 'scrabble',
 'meet',
 'sudoku',
 'unfortunately',
 'really',
 'multiple',
 'word',
 'scramble',
 'word',
 'certain',
 'set',
 'possible',
 'letter',
 'solution',
 'player',
 'must',
 'solve',
 'word',
 'cotemporaneously',
 'approach',
 'one',
 'might',
 'approach',
 'sudoku',
 'really',
 'possible',
 'play',
 'like',
 'electronic',
 'sudoku',
 'make',
 'notation',
 'possible',
 'answer',
 'board',
 'become',
 'nigh',
 'unplayable',
 'difficulty',
 'curve',
 'extremely',
 'uneven',
 'jump',
 'drop',
 'unexpectedly',
 'within',
 'difficulty',
 'head',
 'lexica',
 'also',
 'bill',
 'coffee',
 'break',
 'type',
 'game',
 'due',
 'finite',
 'number',
 'puzzle',
 'available',
 'although',
 'large',
 'number',
 'puzzle',
 'can',
 'not',
 'easily',
 'reset',
 'severely',
 'limits',
 'coffee',
 'break',
 'play',
 'random',
 'puzzle',
 'generator',
 'would',
 'improve',
 'limitation',
 'timer',
 'unnecessary',
 'feature',
 'can',
 'not',
 'reset',
 'puzzle',
 'replay',
 'can',

In [12]:
# save the lematized data, as separate pickle file

import pickle

X_lemmatized_file = Path('dataset_cleaned_heartless_sampled_for_demo_X_lemmatized.pkl')

with open(X_lemmatized_file, "wb") as f:
    pickle.dump(X_lemmatized, f)

In [9]:
import pickle

X_lemmatized_file = Path('dataset_cleaned_heartless_sampled_for_demo_X_lemmatized.pkl')

with open(X_lemmatized_file, "rb") as f:
    X_lemmatized = pickle.load(f)

X_lemmatized[0]

['game',
 'bill',
 'scrabble',
 'meet',
 'sudoku',
 'unfortunately',
 'really',
 'multiple',
 'word',
 'scramble',
 'word',
 'certain',
 'set',
 'possible',
 'letter',
 'solution',
 'player',
 'must',
 'solve',
 'word',
 'cotemporaneously',
 'approach',
 'one',
 'might',
 'approach',
 'sudoku',
 'really',
 'possible',
 'play',
 'like',
 'electronic',
 'sudoku',
 'make',
 'notation',
 'possible',
 'answer',
 'board',
 'become',
 'nigh',
 'unplayable',
 'difficulty',
 'curve',
 'extremely',
 'uneven',
 'jump',
 'drop',
 'unexpectedly',
 'within',
 'difficulty',
 'head',
 'lexica',
 'also',
 'bill',
 'coffee',
 'break',
 'type',
 'game',
 'due',
 'finite',
 'number',
 'puzzle',
 'available',
 'although',
 'large',
 'number',
 'puzzle',
 'can',
 'not',
 'easily',
 'reset',
 'severely',
 'limits',
 'coffee',
 'break',
 'play',
 'random',
 'puzzle',
 'generator',
 'would',
 'improve',
 'limitation',
 'timer',
 'unnecessary',
 'feature',
 'can',
 'not',
 'reset',
 'puzzle',
 'replay',
 'can',

In [34]:
tt = list(map(lambda x: ' '.join(x), X_lemmatized))

In [32]:
# load/create custom stopwords stored in a txt from dataset folder
from pathlib import Path

custom_stopwords_path = Path('../../dataset/topic_modelling/stopwords.txt')
custom_stowords_games_path = Path('../../dataset/topic_modelling/stopwords_games.txt')
game_name_list_path = Path('../../dataset/topic_modelling/game_name_list.txt')

with open(custom_stopwords_path, 'r') as f:
    custom_stopwords = f.read().splitlines()

with open(custom_stowords_games_path, 'r') as f:
    custom_stowords_games = f.read().splitlines()

with open(game_name_list_path, 'r') as f:
    game_name_list = f.read().splitlines()

# also include the stopword list from nltk
from nltk.corpus import stopwords
nltk_stopwords = stopwords.words('english')

custom_stopwords = custom_stopwords + custom_stowords_games + game_name_list + nltk_stopwords
custom_stopwords = set(custom_stopwords)

print(custom_stopwords)
print(len(custom_stopwords))


{'', 'copy kitty ost', 'playhear : square paper city', 'rescue team 5', 'trainz plus dlc - c&o hinton division', 'roll player playtest', 'block robot mini survival game', "freddy fazbear's pizzeria simulator", 'shadows of the cloud demo', 'the wanderer original soundtrack', 'aew: fight forever limitless bunny bundle', 'fantasy grounds - pfrpg the road to revolution: the campaign (pfrpg)', 'project: r.e.b.o.o.t', 'hypt - original soundtrack', 'new retro arcade: neon original soundtrack', '迷失', 'divilixa', 'pixel slayer', 'fantasy grounds - pathfinder rpg - pathfinder flip-mat - classic hill country', 'metrail', 'visual novel maker - cursed kingdoms - twisted forest music pack', 'star trek: infinite - galactic tracks', 'doomed to hell', 'stonedefence', 'sacred 3: orc of thrones', 'blue box game: burgergame', 'guild of dragons', 'epicsurvivors playtest', 'metro conflict: the origin', 'darq: complete edition', 'me && mory', 'couch combat demo', 'ifsunsets playtest', 'aria chronicle', 'robi

In [51]:
# add a sklearn CountVectorizer and select top 2000 words for tm
# ref: https://stackoverflow.com/questions/21552518/using-scikit-learn-vectorizers-and-vocabularies-with-gensim

from sklearn.feature_extraction.text import CountVectorizer, ENGLISH_STOP_WORDS

vect = CountVectorizer(ngram_range=(1, 1), stop_words=list(ENGLISH_STOP_WORDS.union(custom_stopwords)), max_features=2000000)      # default value of max_features in gensim.corpora.Dictionary is 2M
corpus_vect = vect.fit_transform(tt)

corpus = gensim.matutils.Sparse2Corpus(corpus_vect, documents_columns=False)

# transform scikit vocabulary into gensim dictionary
id2word = gensim.corpora.Dictionary.from_corpus(
    corpus,
    id2word=dict((id, word) for word, id in vect.vocabulary_.items())
)

corpus_file = Path(dataset_path.stem + '_corpus.mm')
gensim.corpora.MmCorpus.serialize(str(corpus_file), corpus)

corpus = gensim.corpora.MmCorpus(str(corpus_file))

# save the corpus and reload it as mmcorpus
# this is done within the training loop

/Users/michaelcheng/miniforge3/envs/fyp-test-tm/lib/python3.9/site-packages/sklearn/feature_extraction/text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['00', '000', '00000000000000001', '000001', '001', '00111', '002', '003', '004', '005', '006', '007', '008', '009', '01', '010', '0101', '011', '012', '013', '014', '015', '016', '017', '018', '019', '01d', '01fb', '02', '020', '021', '022', '023', '024', '025', '026', '027', '028', '029', '02a', '02b', '03', '030', '031', '032', '033', '034', '035', '036', '037', '038', '039', '03m', '04', '040', '041', '042', '043', '044', '045', '046', '047', '048', '049', '05', '050', '051', '053', '054', '055', '056', '057', '058', '059', '06', '060', '062', '063', '064', '065', '066', '067', '068', '069', '07', '071', '072', '073', '074', '075', '076', '077', '078', '079', '08', '080', '081', '082', '083', '084', '085', '086', '087', '088', '09', '090', '091', '092',

In [54]:
corpus_vect.todense().shape

(75146, 32242)

In [37]:
# use gensim to build a dictionary and train our LDAModel

id2word = gensim.corpora.Dictionary(X_lemmatized)

corpus = [id2word.doc2bow(text) for text in X_lemmatized]

# save the dictionary and corpus for later use (e.g. hyperparameter selection)

# no need to save the id2word, as it's saved by ldamodel
# id2word_file = Path(dataset_path.stem + '_id2word.dict')
# id2word.save(str(id2word_file))
corpus_file = Path(dataset_path.stem + '_corpus.mm')
gensim.corpora.MmCorpus.serialize(str(corpus_file), corpus)

# load the id2word and corpus
# id2word = gensim.corpora.Dictionary.load(str(id2word_file))
corpus = gensim.corpora.MmCorpus(str(corpus_file))

In [55]:
list(id2word.items())

[(31175, 'werewolf'),
 (24098, 'rid'),
 (29908, 'unicorn'),
 (25281, 'shooting'),
 (13038, 'gun'),
 (3802, 'build'),
 (28024, 'teleporters'),
 (13155, 'hair'),
 (8430, 'dresser'),
 (4323, 'cavern'),
 (27725, 'sword'),
 (25277, 'shoot'),
 (4265, 'cat'),
 (16898, 'lord'),
 (18531, 'moon'),
 (32144, 'yoyo'),
 (25159, 'sharknado'),
 (18161, 'minion'),
 (25734, 'sky'),
 (28054, 'temple'),
 (31898, 'wyverns'),
 (26326, 'spawn'),
 (3960, 'buy'),
 (18856, 'music'),
 (31552, 'wizard'),
 (23290, 'record'),
 (16554, 'like'),
 (21357, 'play'),
 (2603, 'base'),
 (30922, 'want'),
 (9365, 'entirely'),
 (17334, 'marble'),
 (28486, 'thing'),
 (18049, 'minecraft'),
 (7859, 'dimension'),
 (29346, 'trust'),
 (26780, 'start'),
 (16315, 'learning'),
 (28197, 'terrarium'),
 (25560, 'simply'),
 (24587, 'satisfy'),
 (10141, 'experience'),
 (26249, 'sound'),
 (24333, 'rude'),
 (5327, 'compare'),
 (14322, 'imagination'),
 (5942, 'copy'),
 (16822, 'look'),
 (24424, 'sad'),
 (15199, 'introduction'),
 (11616, 'frie

In [ ]:
# test different method to build the corpus for faster training



In [56]:
N_TOPICS = 20

# Online LDA, how to effective train LDA models
# https://papers.nips.cc/paper_files/paper/2010/hash/71f6278d140af599e06ad9bf1ba03cb0-Abstract.html

lda_model = gensim.models.ldamulticore.LdaMulticore(corpus=corpus,
                                             id2word=id2word,
                                             num_topics=N_TOPICS,         # later can use grid search to find the best number of topics
                                             random_state=42,
                                             chunksize=2048,                # chunk size affects memory consumption, and updating speed (like DL batch_size). https://groups.google.com/g/gensim/c/FE7_FYSconA
                                             passes=1,                     # no. of passes over the whole corpus. If larger chunksize, then the passes should be larger too.
                                            #  alpha='auto',
                                             workers=3)     # workers = no. of cores (physical cores, but not logical threads)

visualize the data

In [57]:
import pyLDAvis.gensim_models

pyLDAvis.enable_notebook()
vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, id2word, mds="mmds", R=10)
vis

/Users/michaelcheng/miniforge3/envs/fyp-test-tm/lib/python3.9/site-packages/sklearn/manifold/_mds.py:298: FutureWarning: The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.
  warnings.warn(


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
0     -0.062961  0.130716       1        1  9.873603
4     -0.006299  0.052872       2        1  8.621910
11    -0.007033  0.158052       3        1  7.671166
16    -0.163119 -0.017394       4        1  6.698698
7     -0.051420  0.060356       5        1  6.665809
9      0.105866  0.146844       6        1  6.548516
2      0.010794 -0.094368       7        1  5.953547
19    -0.145013  0.058020       8        1  5.654491
3      0.045768  0.086992       9        1  5.299519
17    -0.008845  0.001981      10        1  5.048240
12    -0.217738 -0.084959      11        1  4.760845
15    -0.089142 -0.059590      12        1  4.678770
18     0.004997  0.088315      13        1  4.489718
1      0.043553 -0.029769      14        1  3.576844
5      0.190996 -0.008469      15        1  3.276304
13     0.103260  0.002258      16        1  2.961549
14     0.151370  0.088849      17        1  2.878040
8      0.172530 -0.189111      18        1  2.047840
10    -0.064109 -0.139697      19        1  1.834615
6     -0.013456 -0.251898      20        1  1.459977, topic_info=          Term          Freq         Total Category  logprob  loglift
394       best   9539.000000   9539.000000  Default  10.0000  10.0000
161       good  13568.000000  13568.000000  Default   9.0000   9.0000
33   minecraft  21959.000000  21959.000000  Default   8.0000   8.0000
27        play  31049.000000  31049.000000  Default   7.0000   7.0000
51       great  12899.000000  12899.000000  Default   6.0000   6.0000
..         ...           ...           ...      ...      ...      ...
142        fun    245.498907  21496.313672  Topic20  -4.0655  -0.2456
972       wait    126.428219   1564.360400  Topic20  -4.7291   1.7112
27        play    190.487610  31049.554296  Topic20  -4.3192  -0.8670
559       come    139.159545   4603.631397  Topic20  -4.6332   0.7278
26        like    134.821998  20046.293003  Topic20  -4.6649  -0.7751

[619 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
9145     13  0.956434  absolutley
8980     19  0.935249  achivments
1723      1  0.027884      addict
1723      2  0.010812      addict
1723      3  0.034712      addict
...     ...       ...         ...
1892      7  0.003201        zone
1892     13  0.012805        zone
1892     15  0.003201        zone
1892     16  0.006403        zone
1892     17  0.137655        zone

[3922 rows x 3 columns], R=10, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 5, 12, 17, 8, 10, 3, 20, 4, 18, 13, 16, 19, 2, 6, 14, 15, 9, 11, 7])

save model

we need to save the corpora.Dictionary and the LDA model

In [14]:
# save the LDA multicore model (and the corpora.Dictionary object) automatically

lda_save_folder = Path(f'lda_model_{datetime.now().strftime("%Y%m%d_%H%M%S")}')
if not lda_save_folder.exists():
    lda_save_folder.mkdir()

lda_model.save(str(lda_save_folder.joinpath('lda_model')))     # no need to add file extension

Evaluation

gensim provide functions to calculate, so we don't need to install octis (as the evaluation backend of octis also relies on gensim)

octis seems awesome for simple development, but it installs many packages ;(

In [41]:
# corpus = lemmatized words (?) (list of list of str)

# create a result object from the LDAMulticore model for octis evaluation
# referencing from https://github.com/MIND-Lab/OCTIS/blob/master/octis/models/LDA.py
# and guideline in README: https://github.com/MIND-Lab/OCTIS/tree/master
result_lda_online = {}
result_lda_online['topic-word-matrix'] = lda_model.get_topics()

top_words = 10
topics_output = []
for topic in result_lda_online["topic-word-matrix"]:
    top_k = np.argsort(topic)[-top_words:]
    top_k_words = list(reversed([id2word[i] for i in top_k]))
    topics_output.append(top_k_words)
result_lda_online["topics"] = topics_output

def _get_topic_document_matrix(lda_model, corpus, num_topics=10):
    """
    Return the topic representation of the
    corpus
    """

    id_corpus = corpus

    doc_topic_tuples = []
    for document in id_corpus:
        doc_topic_tuples.append(
            lda_model.get_document_topics(document, minimum_probability=0))

    topic_document = np.zeros((num_topics, len(doc_topic_tuples)))

    for ndoc in range(len(doc_topic_tuples)):
        document = doc_topic_tuples[ndoc]
        for topic_tuple in document:
            topic_document[topic_tuple[0]][ndoc] = topic_tuple[1]
    return topic_document

result_lda_online['topic-document-matrix'] = _get_topic_document_matrix(lda_model, corpus, num_topics=N_TOPICS)

In [42]:
lda_model.show_topics(num_topics=N_TOPICS, num_words=10, formatted=True, log=False)

[(0,
  '0.031*"game" + 0.017*"mode" + 0.016*"terrarium" + 0.015*"dont" + 0.014*"get" + 0.012*"minecraft" + 0.011*"expert" + 0.011*"really" + 0.011*"make" + 0.010*"hard"'),
 (1,
  '0.089*"game" + 0.040*"get" + 0.023*"play" + 0.020*"time" + 0.017*"really" + 0.015*"good" + 0.013*"fun" + 0.011*"love" + 0.011*"terrarium" + 0.010*"still"'),
 (2,
  '0.036*"game" + 0.015*"world" + 0.014*"item" + 0.013*"minecraft" + 0.013*"terrarium" + 0.013*"boss" + 0.012*"build" + 0.009*"make" + 0.009*"fight" + 0.009*"thing"'),
 (3,
  '0.049*"game" + 0.045*"minecraft" + 0.033*"terrarium" + 0.015*"get" + 0.014*"play" + 0.013*"say" + 0.011*"like" + 0.010*"boss" + 0.008*"hour" + 0.007*"build"'),
 (4,
  '0.068*"game" + 0.040*"hour" + 0.028*"play" + 0.025*"worth" + 0.019*"money" + 0.019*"get" + 0.017*"amaze" + 0.016*"fun" + 0.014*"every" + 0.013*"ok"'),
 (5,
  '0.029*"game" + 0.023*"get" + 0.019*"world" + 0.014*"kill" + 0.014*"thing" + 0.011*"fun" + 0.011*"many" + 0.011*"award" + 0.011*"con" + 0.010*"play"'),
 (6,

In [20]:
# setup: get the model's topics in their native ordering...
all_topics = lda_model.print_topics()
# ...then create a empty list per topic to collect the docs:
docs_per_topic = [[] for _ in all_topics]

# now, for every doc...
for doc_id, doc_bow in enumerate(corpus):
    # ...get its topics...
    doc_topics = lda_model.get_document_topics(doc_bow)
    # ...& for each of its topics...
    for topic_id, score in doc_topics:
        # ...add the doc_id & its score to the topic's doc list
        docs_per_topic[topic_id].append((doc_id, score))

In [24]:
# If you're interested in the top docs per topic, you can further sort each list's pairs by their score

for doc_list in docs_per_topic:
    doc_list.sort(key=lambda id_and_score: id_and_score[1], reverse=True)

In [25]:
print(docs_per_topic[0][:10])

[(2306384, 0.99681187), (2327985, 0.9914269), (1525134, 0.9806092), (1948157, 0.97839916), (1655473, 0.9756402), (1688446, 0.9756334), (1309651, 0.97359663), (1805370, 0.9712106), (2188923, 0.9693497), (2223045, 0.9693483)]


In [45]:
# show top 10 documents for each topic, also the name of the game
for topic_id, docs in enumerate(docs_per_topic):
    print(f'Topic {topic_id + 1}:')
    for doc_id, score in docs[:10]:
        print(f'Game: {dataset.iloc[doc_id]["app_name"]}')
        print(f'Doc ID: {doc_id}')
        print(f'Score: {score}')
        print(f'Doc: {dataset.iloc[doc_id]["review_text"]}')
        print()
    print('\n\n\n\n\n')

Topic 1:
Game: Pillars of Eternity
Doc ID: 2306384
Score: 0.9968118667602539
Doc: Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading reading reading reading Reading reading reading reading reading reading readin

In [41]:
dataset.iloc[1655473]

index                                                     6294630
app_id                                                       8190
app_name                                             Just Cause 2
review_text     It's one big action movie action movie action ...
review_score                                                    1
review_votes                                                    0
Name: 4780759, dtype: object

In [32]:
X[1655473]

"It's one big action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie action movie 9/10"

In [ ]:
result_lda_online['topic-document-matrix'][0]

array([0.00047761, 0.01666767, 0.00135199, ..., 0.0027796 , 0.01250004,
       0.01000022])

In [17]:
lda_model.get_topics().shape

(20, 410296)

In [ ]:
np.sum(result_lda_online['topic-document-matrix'], axis=0)

array([0.99999999, 1.00000001, 0.99999994, ..., 1.00000002, 1.00000001,
       1.00000008])

Evaluation

instead of using octis, we use gensim provided CoherenceModel object,  
as octis also uses this module for calculating the coherence scores

In [43]:
def _get_empty_idxs(X):
    empty_idxs = []
    for i, text in enumerate(X):
        if len(text) == 0:
            empty_idxs.append(i)
    return sorted(empty_idxs, reverse=True)

empty_idxs = _get_empty_idxs(X_lemmatized)
empty_idxs

# remove empty documents from the dataset
# for idx in empty_idxs:
#     del X_lemmatized[idx]


[]

In [58]:
from gensim.models import CoherenceModel

coherence_model_lda = CoherenceModel(model=lda_model, texts=X_lemmatized, dictionary=id2word, coherence='c_v', processes=3)
coherence_cv = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_cv)


Coherence Score:  0.5143100149048595


In [59]:
# Compute Coherence Score using c_npmi
coherence_model_lda = CoherenceModel(model=lda_model, texts=X_lemmatized, dictionary=id2word, coherence='c_npmi', processes=3)
coherence_npmi = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_npmi)


Coherence Score:  -0.0035319477425691755


In [60]:
from gensim.models import CoherenceModel

coherence_model_lda = CoherenceModel(model=lda_model, texts=X_lemmatized, dictionary=id2word, coherence='c_uci', processes=3)
coherence_cv = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_cv)
# Compute Coherence Score using c_npmi
coherence_model_lda = CoherenceModel(model=lda_model, texts=X_lemmatized, dictionary=id2word, coherence='u_mass', processes=3)
coherence_npmi = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_npmi)


Coherence Score:  -0.170341520604348

Coherence Score:  -2.2411366258177465


INFERENCE

inference test

In [ ]:
# inference test

inference_test = ["well its been fun guys, but that's it, no more updates, that one was the last one, there is no longer going to be anymore content for this game anymore, there is no way to replay it as there won't be any updates, nope, that was it, the last update, nothing more, this game has no new ways to experience it as there is no more content updates, nothing new to freshen up the experience, its such a shame that this game has no replay-ability, once you beat the game there is like no point to playing again, as they said guys 1.2 will be they final update. nothing more after 1.2, there is no chance they will make another final update right? several years and final updates later: alright, thats it, no more updates we wont be getting anymore, thats it, nothing more, no more updates, for real this time... oh god, redigit made another tweet.",
                  "keeps forcing me to play it",
'''I will leave the cat here, so that everybody who passes by can pet it and give it a thumbs up and awards
　　　 　　／＞　　フ
　　　 　　| 　_　 _ l
　 　　 　／` ミ＿xノ
　　 　 /　　　 　 |
　　　 /　 ヽ　　 ﾉ
　 　 │　　|　|　|
　／￣|　　 |　|　|
　| (￣ヽ＿_ヽ_)__)
　＼二つ''']

inference_test = cleaning_strlist(inference_test)

inference_test = list(map(lambda x: lemmatization(x), inference_test))

corpus_test = [id2word.doc2bow(text) for text in inference_test]

test_output = lda_model[corpus_test]

test_output

In [ ]:
inference_test[-1]

['leave',
 'cat',
 'everybody',
 'pass',
 'pet',
 'give',
 'thumb',
 'award',
 'l',
 'x']

In [ ]:
# test inference

corpus_test = [id2word.doc2bow(text) for text in inference_test]

output_test = lda_model[corpus_test]

for i in range(len(output_test)):
    # print(sorted(test_output[i], key=lambda x: x[1], reverse=True))
    print(sorted(output_test[i], key=lambda x: x[1], reverse=True))

[(3, 0.60644966), (11, 0.15789744), (13, 0.123749346), (10, 0.08829053), (8, 0.013170155)]
[(10, 0.5038039), (6, 0.27117985), (0, 0.012500903), (1, 0.012500903), (2, 0.012500903), (3, 0.012500903), (4, 0.012500903), (5, 0.012500903), (7, 0.012500903), (8, 0.012500903), (9, 0.012500903), (11, 0.012500903), (12, 0.012500903), (13, 0.012500903), (14, 0.012500903), (15, 0.012500903), (16, 0.012500903), (17, 0.012500903), (18, 0.012500903), (19, 0.012500903)]
[(16, 0.50347227), (11, 0.21316677), (1, 0.11489906), (18, 0.095704)]


load model (both corpora Dictionary and the LDA model)

In [ ]:
del id2word
del lda_model

model_datetime = datetime(2024, 1, 15, 0, 21, 57)
lda_save_folder = Path(f'lda_model_{model_datetime.strftime("%Y%m%d_%H%M%S")}')

# id2word_load = gensim.corpora.Dictionary.load('lda_model.id2word')
id2word_l = gensim.corpora.Dictionary.load(str(lda_save_folder.joinpath('lda_model.id2word')))

lda_model_l = gensim.models.ldamulticore.LdaMulticore.load(str(lda_save_folder.joinpath('lda_model')))

In [ ]:
corpus_test2 = [id2word_l.doc2bow(text) for text in inference_test]

output_test2 = lda_model_l[corpus_test2]

for i in range(len(output_test2)):
    print(sorted(output_test2[i], key=lambda x: x[1], reverse=True))

[(1, 0.32744843), (16, 0.2903514), (15, 0.123242974), (6, 0.09021147), (18, 0.09014924), (5, 0.030303197), (19, 0.023578195), (7, 0.016134478)]
[(1, 0.49804363), (10, 0.2769175), (0, 0.012502159), (2, 0.012502159), (3, 0.012502159), (4, 0.012502159), (5, 0.012502159), (6, 0.012502159), (7, 0.012502159), (8, 0.012502159), (9, 0.012502159), (11, 0.012502159), (12, 0.012502159), (13, 0.012502159), (14, 0.012502159), (15, 0.012502159), (16, 0.012502159), (17, 0.012502159), (18, 0.012502159), (19, 0.012502159)]
[(13, 0.27624068), (7, 0.20502365), (14, 0.13374868), (17, 0.105004296), (11, 0.104988545), (2, 0.10497881)]
